<a href="https://colab.research.google.com/github/JF11579/Plotly_RE/blob/main/SameHouse/Lot_size.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Notes

### Way too many missing land size data afor this to bemeaningful

# Libraries

In [1]:
import pandas as pd
from google.colab import drive  # <<<<<<<<<------
import plotly.express as px
import numpy as np
import plotly.graph_objects as go
import pandas as pd
from sklearn.preprocessing import MinMaxScaler

# Options

In [2]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)

# Data

In [3]:
# Mount Google Drive
from google.colab import drive
drive.mount('/content/drive')

# Change to the directory containing your CSV
%cd /content/drive/MyDrive/DATA/Real_Estate_Data

Mounted at /content/drive
/content/drive/MyDrive/DATA/Real_Estate_Data


In [94]:
houses = pd.read_csv('Combined_data_Februrary_18.csv')

<ipython-input-94-dee981abd164>:1: DtypeWarning:

Columns (19,21,23,24,25,26,28,30,31,34,35,37,38,39,42,43,45,47,48,49,50,51,53,56,57,58,59,61,62,64,74,75,76,78,87,88,91,92,104,106,109,111,113,115,117,122,123,124,125,127,135,142,143,144,151,152,154,156,158,160,161,164,167,174,180,181,184,185,187,188,189,190,191,192,193,194,199,200,202,203,208,214,216,217,220,221,222,223,227,228,231,232,233,234,235,237) have mixed types. Specify dtype option on import or set low_memory=False.



In [95]:
houses.head()

Address           Town    Zip State      Style      ML#  \
0      19 Winans Place  Locust Valley  11560    NY       Cape  1870802   
1       59 11th Street  Locust Valley  11560    NY   Colonial  2745482   
2  19 White Spots Lane  Locust Valley  11560    NY   Exp Cape  2427641   
3       5 Quarry  Road  Locust Valley  11560    NY  Exp Ranch  2396870   
4        3 Nassau Road  Locust Valley  11560    NY   Colonial  2030725   

   Sold_Price  Baths_Full  Baths_Half  Bath  Bedrooms Appearance  REO  \
0    459000.0         2.0         0.0  2.00       4.0  Excellent  NaN   
1    360000.0         2.0         0.0  2.00       4.0       Good    N   
2    650000.0         2.0         1.0  2.50       3.0       Mint    N   
3    800000.0         3.0         0.0  3.00       4.0  Excellent    N   
4    467500.0         2.0         2.0  2.55       4.0  Diamond!!    N   

  School_District_Name  Approx_Int_Square_Footage  Street_Name Contract_Date  \
0        Locust Valley                        NaN       Winans     9/14/2006   
1        Locust Valley                        NaN         11th    11/23/2015   
2        Locust Valley                     2353.0  White Spots    10/08/2011   
3        Locust Valley                     2151.0      Quarry      5/03/2012   
4        Locust Valley                        NaN       Nassau     6/22/2008   

   Lot_Square_Footage  Lot_Size Contract Date    Year Air_Conditioning  Acres  \
0              7500.0  50 X 150    2006-09-14  2006.0              NaN    NaN   
1              5564.0  57 X 107    2015-11-23  2015.0              NaN    NaN   
2             10492.0      0.24    2011-10-08  2011.0              NaN    NaN   
3             27007.0       .62    2012-05-03  2012.0              NaN    NaN   
4              6098.0    62X100    2008-06-22  2008.0              NaN    NaN   

  Property_Description Agency Also_For_Rent Interior_Features  Apt#  \
0                  NaN    NaN           NaN               NaN   NaN   
1                  NaN    NaN           NaN               NaN   NaN   
2                  NaN    NaN           NaN               NaN   NaN   
3                  NaN    NaN           NaN               NaN   NaN   
4                  NaN    NaN           NaN               NaN   NaN   

  Attic_Description  Auxiliary_Rooms Buyer_Agency_Compensation  \
0               NaN              NaN                       NaN   
1               NaN              NaN                       NaN   
2               NaN              NaN                       NaN   
3               NaN              NaN                       NaN   
4               NaN              NaN                       NaN   

  Waterfront_Features  Building  Building_Permit Block Listing_Broker_Phone_#  \
0                 NaN       NaN              NaN   NaN                    NaN   
1                 NaN       NaN              NaN   NaN                    NaN   
2                 NaN       NaN              NaN   NaN                    NaN   
3                 NaN       NaN              NaN   NaN                    NaN   
4                 NaN       NaN              NaN   NaN                    NaN   

   Branch Modifications_Exclusions Basement_Description Room_Level  \
0     NaN                      NaN                  NaN        NaN   
1     NaN                      NaN                  NaN        NaN   
2     NaN                      NaN                  NaN        NaN   
3     NaN                      NaN                  NaN        NaN   
4     NaN                      NaN                  NaN        NaN   

   Business_Age  Business_Type Utilities_Included Included  Cash_Down  \
0           NaN            NaN                NaN      NaN        NaN   
1           NaN            NaN                NaN      NaN        NaN   
2           NaN            NaN                NaN      NaN        NaN   
3           NaN            NaN                NaN      NaN        NaN   
4           NaN            NaN                NaN      NaN        

# PRe Process

In [96]:
#  'Lot_Square_Footage', 'Lot_Size',

data = houses

data = data.dropna(subset=["Sold_Price"]).query("`Sold_Price` != 0")
data = data[['Address', 'Town','Zip','State','Style',
                    'ML#','Sold_Price','Baths_Full', 'Baths_Half',
                    'Bath','Bedrooms',
                      'Appearance','REO' , 'School_District_Name',
                 'Approx_Int_Square_Footage','Street_Name','Contract_Date', 'Lot_Square_Footage', 'Lot_Size']]


data= data.loc[data.Town.isin(['Roosevelt', 'Hempstead', 'Freeport', 'Farmingdale', 'Mineola','Westbury', 'Roslyns', 'Port Washington', 'Locust Valley'])]


# Convert 'Contract_Date' to datetime
data['Contract_Date'] = pd.to_datetime(data['Contract_Date'])

# Extract the year
data['Year'] = data['Contract_Date'].dt.year


# Drop rows where 'Year' is NaN
data = data.dropna(subset=['Year'])

# Now convert 'Year' to integer
#data['Year'] = data['Year'].astype(int)
####
median_sold_price_all = data.groupby(['Town', 'Year'])['Sold_Price'].median().reset_index()
median_sold_price_all.rename(columns={'Sold_Price': 'Median_Sold_Price_All'}, inplace=True)
#
median_sold_non_ranch = data[data['Style'] != 'Ranch'].groupby(['Town', 'Year'])['Sold_Price'].median().reset_index()
median_sold_non_ranch.rename(columns={'Sold_Price': 'Median_Sold_Non_Ranch'}, inplace=True)
#
median_sold_ranch = data[data['Style'] == 'Ranch'].groupby(['Town', 'Year'])['Sold_Price'].median().reset_index()
median_sold_ranch.rename(columns={'Sold_Price': 'Median_Sold_Ranch'}, inplace=True)

#######
# Merge Median_Sold_Price_All
data = data.merge(median_sold_price_all, on=['Town', 'Year'], how='left')

# Merge Median_Sold_Non_Ranch
data = data.merge(median_sold_non_ranch, on=['Town', 'Year'], how='left')

# Merge Median_Sold_Ranch
data = data.merge(median_sold_ranch, on=['Town', 'Year'], how='left')

houses = data

houses['Month_Year'] = houses['Contract_Date'].dt.strftime('%B-%Y')

In [97]:
houses.head()

Address           Town    Zip State      Style      ML#  \
0      19 Winans Place  Locust Valley  11560    NY       Cape  1870802   
1       59 11th Street  Locust Valley  11560    NY   Colonial  2745482   
2  19 White Spots Lane  Locust Valley  11560    NY   Exp Cape  2427641   
3       5 Quarry  Road  Locust Valley  11560    NY  Exp Ranch  2396870   
4        3 Nassau Road  Locust Valley  11560    NY   Colonial  2030725   

   Sold_Price  Baths_Full  Baths_Half  Bath  Bedrooms Appearance  REO  \
0    459000.0         2.0         0.0  2.00       4.0  Excellent  NaN   
1    360000.0         2.0         0.0  2.00       4.0       Good    N   
2    650000.0         2.0         1.0  2.50       3.0       Mint    N   
3    800000.0         3.0         0.0  3.00       4.0  Excellent    N   
4    467500.0         2.0         2.0  2.55       4.0  Diamond!!    N   

  School_District_Name  Approx_Int_Square_Footage  Street_Name Contract_Date  \
0        Locust Valley                        NaN       Winans    2006-09-14   
1        Locust Valley                        NaN         11th    2015-11-23   
2        Locust Valley                     2353.0  White Spots    2011-10-08   
3        Locust Valley                     2151.0      Quarry     2012-05-03   
4        Locust Valley                        NaN       Nassau    2008-06-22   

   Lot_Square_Footage  Lot_Size    Year  Median_Sold_Price_All  \
0              7500.0  50 X 150  2006.0               609500.0   
1              5564.0  57 X 107  2015.0               485000.0   
2             10492.0      0.24  2011.0               666000.0   
3             27007.0       .62  2012.0               550000.0   
4              6098.0    62X100  2008.0               545000.0   

   Median_Sold_Non_Ranch  Median_Sold_Ranch      Month_Year  
0               610000.0           520000.0  September-2006  
1               515000.0           440000.0   November-2015  
2               770000.0           361000.0    October-2011  
3               512500.0           717800.0        May-2012  
4               582500.0           302500.0       June-2008

In [98]:
houses.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 26087 entries, 0 to 26086
Data columns (total 24 columns):
 #   Column                     Non-Null Count  Dtype         
---  ------                     --------------  -----         
 0   Address                    26087 non-null  object        
 1   Town                       26087 non-null  object        
 2   Zip                        26087 non-null  int64         
 3   State                      26087 non-null  object        
 4   Style                      26085 non-null  object        
 5   ML#                        26087 non-null  object        
 6   Sold_Price                 26087 non-null  float64       
 7   Baths_Full                 26087 non-null  float64       
 8   Baths_Half                 26086 non-null  float64       
 9   Bath                       26080 non-null  float64       
 10  Bedrooms                   26087 non-null  float64       
 11  Appearance                 20299 non-null  object        
 12  REO 

In [99]:
# '40 x 100', '80 x 100', '100 x 100', '1/2 acre', '1 acre', '2 acres', '2 acres +']

In [100]:
#bin_edges = [0,4000, 8000, 10000, 20000, 43264, 86528, 1730560]

In [101]:
#bin_labels = ['40 x 100', '80 x 100', '100 x 100' , '1/2 acre', '1 acre', '2 acres', '2 acres +' ]

In [102]:
import pandas as pd

# Correctly defined bin edges and labels based on your categories
bin_edges = [0, 4000, 8000, 10000, 20000, 43264, 86528, 1730560]
bin_labels = ['40 x 100', '80 x 100', '100 x 100', '1/2 acre', '1 acre', '2 acres', '2 acres +']

# Bin the lot sizes using the 'Lot_Square_Footage' column
houses['Lot_Size_Category'] = pd.cut(houses['Lot_Square_Footage'], bins=bin_edges, labels=bin_labels, right=False)

# Calculate counts for each category within each town
category_counts = houses.groupby(['Town', 'Lot_Size_Category']).size().reset_index(name='Count')

# Calculate the total counts for each town to use for percentage calculation
total_counts_per_town = category_counts.groupby('Town')['Count'].transform('sum')
category_counts['Percentage'] = (category_counts['Count'] / total_counts_per_town) * 100


In [103]:
houses.head()

Address           Town    Zip State      Style      ML#  \
0      19 Winans Place  Locust Valley  11560    NY       Cape  1870802   
1       59 11th Street  Locust Valley  11560    NY   Colonial  2745482   
2  19 White Spots Lane  Locust Valley  11560    NY   Exp Cape  2427641   
3       5 Quarry  Road  Locust Valley  11560    NY  Exp Ranch  2396870   
4        3 Nassau Road  Locust Valley  11560    NY   Colonial  2030725   

   Sold_Price  Baths_Full  Baths_Half  Bath  Bedrooms Appearance  REO  \
0    459000.0         2.0         0.0  2.00       4.0  Excellent  NaN   
1    360000.0         2.0         0.0  2.00       4.0       Good    N   
2    650000.0         2.0         1.0  2.50       3.0       Mint    N   
3    800000.0         3.0         0.0  3.00       4.0  Excellent    N   
4    467500.0         2.0         2.0  2.55       4.0  Diamond!!    N   

  School_District_Name  Approx_Int_Square_Footage  Street_Name Contract_Date  \
0        Locust Valley                        NaN       Winans    2006-09-14   
1        Locust Valley                        NaN         11th    2015-11-23   
2        Locust Valley                     2353.0  White Spots    2011-10-08   
3        Locust Valley                     2151.0      Quarry     2012-05-03   
4        Locust Valley                        NaN       Nassau    2008-06-22   

   Lot_Square_Footage  Lot_Size    Year  Median_Sold_Price_All  \
0              7500.0  50 X 150  2006.0               609500.0   
1              5564.0  57 X 107  2015.0               485000.0   
2             10492.0      0.24  2011.0               666000.0   
3             27007.0       .62  2012.0               550000.0   
4              6098.0    62X100  2008.0               545000.0   

   Median_Sold_Non_Ranch  Median_Sold_Ranch      Month_Year Lot_Size_Category  
0               610000.0           520000.0  September-2006          80 x 100  
1               515000.0           440000.0   November-2015          80 x 100  
2               770000.0           361000.0    October-2011          1/2 acre  
3               512500.0           717800.0        May-2012            1 acre  
4               582500.0           302500.0       June-2008          80 x 100

In [104]:
import plotly.graph_objects as go

# Assuming 'category_counts' is prepared with the counts for each town within each lot size category

# Initialize an empty figure
fig = go.Figure()

# To manage legend entries for towns, keep track of which towns have been added
legend_added = set()

# Iterate over each lot size category to add bars
for lot_size in bin_labels:
    # Filter the DataFrame for the current lot size category
    lot_size_data = category_counts[category_counts['Lot_Size_Category'] == lot_size]

    # Calculate the total count for this lot size category to determine proportions
    total_count = lot_size_data['Count'].sum()

    for _, row in lot_size_data.iterrows():
        town = row['Town']
        count = row['Count']

        # Calculate the proportion of this town's count within the lot size category
        proportion = (count / total_count) * 100  # Proportion of the total

        show_legend = town not in legend_added
        if show_legend:
            legend_added.add(town)

        fig.add_trace(go.Bar(
            name=town,
            x=[lot_size],
            y=[proportion],
            marker_color=color_dict.get(town, 'grey'),
            text=f"{count}",
            textposition='inside',
            hoverinfo='text+name',
            showlegend=show_legend
        ))

# Customize layout
fig.update_layout(
    barmode='stack',
    title="Proportional Distribution of Towns by Lot Size Category",
    xaxis_title="Lot Size Category",
    yaxis_title="Proportion (%)",
    legend_title="Town",
    uniformtext_minsize=8,  # Adjust text size inside bars if necessary
    uniformtext_mode='hide'  # Hide text if it doesn't fit
)

###############################################
##### Economist-style customizations
economist_red = '#e3120b'
background_color = 'rgb(195, 215, 227)'
font_family = "Arial, sans-serif"

fig.update_layout(
    title={'text': "Average Household Income", 'y':0.9, 'x':0.5, 'xanchor': 'center', 'yanchor': 'top'},
    title_font=dict(size=18, color=economist_red, family=font_family),
    plot_bgcolor=background_color,
    paper_bgcolor=background_color,
    font=dict(color='black', family=font_family),
    legend_title="House Styles"
)
###############################################

# Show the plot
fig.show()


# Scatter plot

In [114]:
houses.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 26087 entries, 0 to 26086
Data columns (total 26 columns):
 #   Column                     Non-Null Count  Dtype         
---  ------                     --------------  -----         
 0   Address                    26087 non-null  object        
 1   Town                       26087 non-null  object        
 2   Zip                        26087 non-null  int64         
 3   State                      26087 non-null  object        
 4   Style                      26085 non-null  object        
 5   ML#                        26087 non-null  object        
 6   Sold_Price                 26087 non-null  float64       
 7   Baths_Full                 26087 non-null  float64       
 8   Baths_Half                 26086 non-null  float64       
 9   Bath                       26080 non-null  float64       
 10  Bedrooms                   26087 non-null  float64       
 11  Appearance                 20299 non-null  object        
 12  REO 

In [115]:
houses.head()

Address           Town    Zip State      Style      ML#  \
0      19 Winans Place  Locust Valley  11560    NY       Cape  1870802   
1       59 11th Street  Locust Valley  11560    NY   Colonial  2745482   
2  19 White Spots Lane  Locust Valley  11560    NY   Exp Cape  2427641   
3       5 Quarry  Road  Locust Valley  11560    NY  Exp Ranch  2396870   
4        3 Nassau Road  Locust Valley  11560    NY   Colonial  2030725   

   Sold_Price  Baths_Full  Baths_Half  Bath  Bedrooms Appearance  REO  \
0    459000.0         2.0         0.0  2.00       4.0  Excellent  NaN   
1    360000.0         2.0         0.0  2.00       4.0       Good    N   
2    650000.0         2.0         1.0  2.50       3.0       Mint    N   
3    800000.0         3.0         0.0  3.00       4.0  Excellent    N   
4    467500.0         2.0         2.0  2.55       4.0  Diamond!!    N   

  School_District_Name  Approx_Int_Square_Footage  Street_Name Contract_Date  \
0        Locust Valley                        NaN       Winans    2006-09-14   
1        Locust Valley                        NaN         11th    2015-11-23   
2        Locust Valley                     2353.0  White Spots    2011-10-08   
3        Locust Valley                     2151.0      Quarry     2012-05-03   
4        Locust Valley                        NaN       Nassau    2008-06-22   

   Lot_Square_Footage  Lot_Size    Year  Median_Sold_Price_All  \
0              7500.0  50 X 150  2006.0               609500.0   
1              5564.0  57 X 107  2015.0               485000.0   
2             10492.0      0.24  2011.0               666000.0   
3             27007.0       .62  2012.0               550000.0   
4              6098.0    62X100  2008.0               545000.0   

   Median_Sold_Non_Ranch  Median_Sold_Ranch      Month_Year Lot_Size_Category  \
0               610000.0           520000.0  September-2006          80 x 100   
1               515000.0           440000.0   November-2015          80 x 100   
2               770000.0           361000.0    October-2011          1/2 acre   
3               512500.0           717800.0        May-2012            1 acre   
4               582500.0           302500.0       June-2008          80 x 100   

   jittered_x  
0    0.913842  
1    0.935957  
2    2.956404  
3    3.954111  
4    0.918101

In [137]:
import plotly.graph_objects as go
import numpy as np
import pandas as pd

# Example DataFrame initialization (replace with your actual 'houses' DataFrame)
# df = houses

# Define bin labels and color mapping
bin_labels = ['40 x 100', '80 x 100', '100 x 100', '1/2 acre', '1 acre', '2 acres', '2 acres +']
color_dict = {
    'Roslyns': '#006400',  # DarkGreen
    'Port Washington': '#008000',  # Green
    'Locust Valley': '#90EE90',  # LightGreen
    'Mineola': '#00008B',  # DarkBlue
    'Westbury': '#0000FF',  # Blue
    'Farmingdale': '#ADD8E6',  # LightBlue
    'Freeport': '#8B0000',  # DarkRed
    'Hempstead': '#FF0000',  # Red
    'Roosevelt': '#F08080'  # LightCoral
}

# Map bin labels to numeric indices
bin_label_mapping = {label: i for i, label in enumerate(bin_labels)}

# Adjust jitter magnitude
jitter = 0.7

# Apply mapping and add jitter
df['category_index'] = df['Lot_Size_Category'].map(bin_label_mapping)
df['jittered_x'] = df['category_index'].astype(float) + (np.random.rand(len(df)) - 0.5) * jitter

# Initialize an empty figure
fig = go.Figure()

# Iterate over each town to plot data
for town, color in color_dict.items():
    # Filter data for the current town
    town_data = df[df['Town'] == town]

    fig.add_trace(go.Scatter(
        x=town_data['jittered_x'],
        y=np.random.rand(len(town_data)),  # Dummy Y-axis values
        mode='markers',
        marker=dict(color=color, size=10),
        name=town,
        hovertemplate='Town: %{text}<br>Lot Size Category: %{meta}<extra></extra>',
        text=town_data['Town'],  # Shows town name on hover
        meta=town_data['Lot_Size_Category'],  # Additional data to display on hover
    ))

# Customize the x-axis to show bin labels
fig.update_xaxes(
    tickvals=list(bin_label_mapping.values()),  # Numerical indices for each bin label
    ticktext=bin_labels  # Actual text labels for the bins
)

# Customize layout
fig.update_layout(
    title="Distribution of Properties by Lot Size Category",
    xaxis_title="Lot Size Category",
    yaxis_title="",
    yaxis=dict(showticklabels=False),  # Optionally hide Y-axis labels as they're not meaningful
    legend_title="Town"
)

###############################################
##### Economist-style customizations
economist_red = '#e3120b'
background_color = 'rgb(195, 215, 227)'
font_family = "Arial, sans-serif"

fig.update_layout(
    title={'text': "Few Towns Have the Biggest Lot Sizes", 'y':0.9, 'x':0.5, 'xanchor': 'center', 'yanchor': 'top'},
    title_font=dict(size=18, color=economist_red, family=font_family),
    plot_bgcolor=background_color,
    paper_bgcolor=background_color,
    font=dict(color='black', family=font_family),
    legend_title="House Styles"
)
###############################################

# Show the plot
fig.show()


In [ ]:
#########

In [128]:
import plotly.graph_objects as go
import numpy as np

df = houses  # Ensure 'houses' DataFrame is correctly prepared with 'Lot_Size_Category'

# Correctly defined color dictionary
color_dict = {
    'Roslyns': '#006400',  # DarkGreen
    'Port_Washington': '#008000',  # Green
    'Locust_Valley': '#90EE90',  # LightGreen
    'Mineola': '#00008B',  # DarkBlue
    'Westbury': '#0000FF',  # Blue
    'Farmingdale': '#ADD8E6',  # LightBlue
    'Freeport': '#8B0000',  # DarkRed
    'Hempstead': '#FF0000',  # Red
    'Roosevelt': '#F08080'  # LightCoral
}

# Initialize necessary variables
jitter = 0.8  # Adjust jitter magnitude here
bin_labels = ['40 x 100', '80 x 100', '100 x 100', '1/2 acre', '1 acre', '2 acres', '2 acres +']  # Example bin labels
bin_label_mapping = {label: i for i, label in enumerate(bin_labels)}

# Correct mapping and ensure the result is numeric before adding jitter
df['category_index'] = df['Lot_Size_Category'].map(bin_label_mapping)
df['jittered_x'] = df['category_index'].astype(float) + (np.random.rand(len(df)) - 0.5) * jitter

# Initialize an empty figure
fig = go.Figure()

# Iterate over each town to plot data
for town, color in color_dict.items():
    # Filter data for the current town
    town_data = df[df['Town'] == town]

    fig.add_trace(go.Scatter(
        x=town_data['jittered_x'],
        y=np.random.rand(len(town_data)),  # Dummy Y-axis values for illustration
        mode='markers',
        marker=dict(color=color, size=10),
        name=town,
        hovertemplate='Town: %{text}<br>Lot Size Category: %{meta}<br><extra></extra>',
        text=town_data['Town'],  # Shows town name on hover
        meta=town_data['Lot_Size_Category'],  # Additional data to display on hover
    ))

# Customize the x-axis and layout as previously described
# (No changes needed here from your provided script)

# Show the plot
fig.show()


In [132]:
bin_label_mapping = {label: i for i, label in enumerate(bin_labels)}
df['category_index'] = df['Lot_Size_Category'].map(bin_label_mapping)
df['jittered_x'] = df['category_index'].astype(float) + (np.random.rand(len(df)) - 0.5) * jitter
fig.update_xaxes(
    tickvals=list(bin_label_mapping.values()),  # Numerical indices
    ticktext=bin_labels  # Corresponding labels
)


In [129]:
#bin_label_mapping = {label: i for i, label in enumerate(bin_labels)}


In [130]:
# df['category_index'] = df['Lot_Size_Category'].map(bin_label_mapping)
# df['jittered_x'] = df['category_index'].astype(float) + (np.random.rand(len(df)) - 0.5) * jitter


In [133]:
fig.update_xaxes(
    tickvals=list(bin_label_mapping.values()),  # Numerical indices
    ticktext=bin_labels  # Corresponding labels
)
###############################################
##### Economist-style customizations
economist_red = '#e3120b'
background_color = 'rgb(195, 215, 227)'
font_family = "Arial, sans-serif"

fig.update_layout(
    title={'text': "Few Towns Have the Biggest Lot Sizes", 'y':0.9, 'x':0.5, 'xanchor': 'center', 'yanchor': 'top'},
    title_font=dict(size=18, color=economist_red, family=font_family),
    plot_bgcolor=background_color,
    paper_bgcolor=background_color,
    font=dict(color='black', family=font_family),
    legend_title="House Styles"
)
###############################################

In [117]:
import plotly.graph_objects as go
import numpy as np

df = houses

# Correct mapping and ensure the result is numeric before adding jitter
df['jittered_x'] = df['Lot_Size_Category'].map(bin_label_mapping).astype(float) + (np.random.rand(len(df)) - 0.9) * jitter
# Assuming 'df' has been binned into 'Lot_Size_Category' and has a 'Town' column

# Initialize an empty figure
fig = go.Figure()

# Map bin labels to numeric values to facilitate jitter and then back to labels for plotting
bin_label_mapping = {label: i for i, label in enumerate(bin_labels)}




# Add jitter: Generate random offsets
#jitter = 0.1  # Adjust jitter magnitude here
#df['jittered_x'] = df['Lot_Size_Category'].map(bin_label_mapping) + (np.random.rand(len(df)) - 0.5) * jitter

# Plot each town as a separate trace to utilize the color mapping
for town, color in color_dict.items():
    # Filter data for the current town
    town_data = df[df['Town'] == town]

    # Add scatter plot for this town
    fig.add_trace(go.Scatter(
        x=town_data['jittered_x'],
        y=np.random.rand(len(town_data)),  # Dummy Y-axis values, since focus is on x-axis distribution
        mode='markers',
        marker_color=color,
        name=town,
        text=town_data['Lot_Size_Category'],  # Show lot size category on hover
        hoverinfo='text'
    ))

# Customize the x-axis to show the bin labels
fig.update_xaxes(
    tickvals=list(bin_label_mapping.values()),
    ticktext=bin_labels
)

# Customize layout
fig.update_layout(
    title="Distribution of Properties by Lot Size Category",
    xaxis_title="Lot Size",
    yaxis_title=")",
    yaxis=dict(showticklabels=False),  # Hide y-axis tick labels as they're not meaningful in this context
    legend_title="Town"
)

###############################################
##### Economist-style customizations
economist_red = '#e3120b'
background_color = 'rgb(195, 215, 227)'
font_family = "Arial, sans-serif"

fig.update_layout(
    title={'text': "Few Towns Have the Biggest Lot Sizes", 'y':0.9, 'x':0.5, 'xanchor': 'center', 'yanchor': 'top'},
    title_font=dict(size=18, color=economist_red, family=font_family),
    plot_bgcolor=background_color,
    paper_bgcolor=background_color,
    font=dict(color='black', family=font_family),
    legend_title="House Styles"
)
###############################################

# Show the plot
fig.show()


In [118]:
 a = b

NameError: name 'b' is not defined

# tuesday

In [ ]:
# '40 x 100' ,'80 x 100' , '100 x 100', '1/2 acre' ,'1 acre','2 acres', '2 acres +'

##Trying to make a scatterplot with categorical x axis

In [ ]:
# prompt: houses.info()

houses.info()


In [ ]:
import plotly.graph_objects as go
import numpy as np
import pandas as pd

# Corrected category array including '40 x 80' and '2 acres +'
categoryarray = ['40 x 80', '40 x 100', '80 x 100', '100 x 100', '1/2 acre', '1 acre', '2 acres', '2 acres +']

# Assuming 'houses' is your DataFrame and is already loaded
# Ensure 'Lot_Size' is categorized correctly, and add jitter
houses['jittered_index'] = houses['Lot_Size'].apply(lambda x: categoryarray.index(x) if x in categoryarray else np.nan) + \
                           np.random.uniform(-0.3, 0.3, houses.shape[0])

# Provided color mapping
color_dict = {
    'Roslyns': '#006400',  # DarkGreen
    'Port Washington': '#008000',  # Green
    'Locust Valley': '#90EE90',  # LightGreen
    'Mineola': '#00008B',  # DarkBlue
    'Westbury': '#0000FF',  # Blue
    'Farmingdale': '#ADD8E6',  # LightBlue
    'Freeport': '#8B0000',  # DarkRed
    'Hempstead': '#FF0000',  # Red
    'Roosevelt': '#F08080'  # LightCoral
}

# Plotting
fig = go.Figure()

for town, color in color_dict.items():
    df_town = houses[houses['Town'] == town]
    fig.add_trace(go.Scattergl(x=df_town['jittered_index'], y=df_town['Sold_Price'],
                               mode='markers', name=town,
                               marker=dict(color=color)))

fig.update_layout(
    xaxis=dict(
        title="Lot Size Categories",
        tickmode='array',
        tickvals=list(range(len(categoryarray))),
        ticktext=categoryarray
    ),
    title='Sold Price vs Lot Size Category',
    yaxis_title="Sold Price",
    legend_title="Town"
)

fig.show()



In [ ]:
# Find unique Lot_Size values not in categoryarray
unmatched_lot_sizes = set(houses['Lot_Square_Footage'].unique()) - set(categoryarray)
print("Unmatched Lot Sizes:", unmatched_lot_sizes)


In [ ]:
print(houses.columns)


In [ ]:
#######

In [ ]:
import plotly.graph_objects as go
import pandas as pd
import numpy as np

# Assuming 'houses' DataFrame exists with 'Town', 'Lot_Size_Category', and 'Sold_Price'
# Your specified color mapping
color_dict = {
    'Roslyns': '#006400',  # DarkGreen
    'Port Washington': '#008000',  # Green
    'Locust Valley': '#90EE90',  # LightGreen
    'Mineola': '#00008B',  # DarkBlue
    'Westbury': '#0000FF',  # Blue
    'Farmingdale': '#ADD8E6',  # LightBlue
    'Freeport': '#8B0000',  # DarkRed
    'Hempstead': '#FF0000',  # Red
    'Roosevelt': '#F08080'  # LightCoral
}

# Categories and their numeric mapping for jitter application
categories = ['40 x 100', '80 x 100', '100 x 100', '1/2 acre', '1 acre', '2 acres', '2 acres +']
category_mapping = {cat: i for i, cat in enumerate(categories)}

# Apply jitter: Assign numeric values for x-axis based on category mapping, then add jitter
jitter_amount = 0.1  # Adjust jitter amount as needed
houses['jittered_x_value'] = houses['Lot_Size_Category'].map(category_mapping) + np.random.uniform(-jitter_amount, jitter_amount, size=len(houses))

# Initialize an empty figure
fig = go.Figure()

# Add scatter plot traces, one for each town, using jittered x values
for town in houses['Town'].unique():
    df_subset = houses[houses['Town'] == town]
    fig.add_trace(go.Scatter(
        # Convert numeric x values back to category labels with jitter applied
        x=[categories[int(x)] for x in df_subset['jittered_x_value'].round()],
        y=df_subset['Sold_Price'],
        mode='markers',
        marker=dict(color=color_dict[town]),
        name=town
    ))

# Customize layout
fig.update_layout(
    title="Sold Price by Lot Size Category with Jitter",
    xaxis=dict(
        title='Lot Size Category',
        type='category',
        categoryorder='array',
        categoryarray=categories  # Custom order for x-axis labels
    ),
    yaxis=dict(
        title='Sold Price'
    ),
    legend_title="Town",
    plot_bgcolor='rgb(255, 255, 255)',
    paper_bgcolor='rgb(255, 255, 255)'
)

# Show the plot
fig.show()


In [ ]:
import plotly.graph_objects as go
import pandas as pd
import numpy as np

# Assuming 'houses' is your DataFrame with relevant data
# Example data setup (replace with your actual DataFrame)
np.random.seed(0)  # For consistent random results
houses = pd.DataFrame({
    'Town': np.random.choice(['Roslyns', 'Port Washington', 'Locust Valley', 'Mineola', 'Westbury', 'Farmingdale', 'Freeport', 'Hempstead', 'Roosevelt'], size=100),
    'Lot_Size_Category': np.random.choice(['40 x 100', '80 x 100', '100 x 100', '1/2 acre', '1 acre', '2 acres', '2 acres +'], size=100),
    'Sold_Price': np.random.uniform(200000, 2000000, size=100)  # Example continuous variable
})

# Your specified color mapping
color_dict = {
    'Roslyns': '#006400',  # DarkGreen
    'Port Washington': '#008000',  # Green
    'Locust Valley': '#90EE90',  # LightGreen
    'Mineola': '#00008B',  # DarkBlue
    'Westbury': '#0000FF',  # Blue
    'Farmingdale': '#ADD8E6',  # LightBlue
    'Freeport': '#8B0000',  # DarkRed
    'Hempstead': '#FF0000',  # Red
    'Roosevelt': '#F08080'  # LightCoral
}

# Initialize an empty figure
fig = go.Figure()

# Add scatter plot traces, one for each town
for town in houses['Town'].unique():
    df_subset = houses[houses['Town'] == town]
    fig.add_trace(go.Scatter(
        x=df_subset['Lot_Size_Category'],
        y=df_subset['Sold_Price'],
        mode='markers',
        marker=dict(color=color_dict[town]),
        name=town
    ))

# Customize layout
fig.update_layout(
    title="Sold Price by Lot Size Category",
    xaxis=dict(
        title='Lot Size Category',
        type='category',
        categoryorder='array',
        categoryarray=['40 x 100', '80 x 100', '100 x 100', '1/2 acre', '1 acre', '2 acres', '2 acres +']  # Custom order for x-axis labels
    ),
    yaxis=dict(
        title='Sold Price'
    ),
    legend_title="Town",
    plot_bgcolor='rgb(255, 255, 255)',
    paper_bgcolor='rgb(255, 255, 255)'
)

# Show the plot
fig.show()


In [ ]:
tick_positions = [0.5, 1.5, 2.5, 3.5, 4.5, 5.5, 6.5]  # Adjust positions as needed

fig.update_layout(
    xaxis=dict(
        title="Lot Size Categories",
        tickmode='array',
        tickvals=tick_positions,
        ticktext=categoryarray,
    ),
    # ... other layout updates
)


In [ ]:
categoryarray=['40 x 100', '80 x 100', '100 x 100', '1/2 acre', '1 acre', '2 acres', '2 acres +']
#
# Assuming fig is your plotly.graph_objects.Figure object

# Update the layout to correctly include all categories on the x-axis
fig.update_layout(
    xaxis=dict(
        title="Lot Size Categories",
        tickmode='array',
        tickvals=list(range(len(categoryarray))),  # Ensures a tick value for each category
        ticktext=categoryarray  # Sets the tick text to your categories
    ),
    title='Sold Price vs Lot Size Category',
    yaxis_title="Sold Price",
    legend_title="Town"
)

fig.show()


In [ ]:
#########

In [ ]:
categoryarray=['40 x 100', '80 x 100', '100 x 100', '1/2 acre', '1 acre', '2 acres', '2 acres +']
#
# Assuming the fig variable is your plotly.graph_objects.Figure instance from earlier

# Update the layout to set the x-axis labels to your new categories
fig.update_layout(
    xaxis=dict(
        title="Lot Size Categories",
        tickmode='array',
        tickvals=list(range(len(categoryarray))),  # Assign a numeric value to each new category
        ticktext=categoryarray  # Use the new categories as tick labels
    ),
    # Keeping the rest of the layout updates as they were
    title='Sold Price vs Lot Size Category with Jitter',
    yaxis_title="Sold Price",
    legend_title="Town"
)

fig.show()



In [ ]:
##########

In [ ]:
# Customize layout
fig.update_layout(
    barmode='stack',
    title="Lot Size and Town",
    xaxis_title='Lot Size',
    yaxis_title='Percentage',
    legend_title='Town',
    xaxis=dict(
        type='category',
        categoryorder='array',
        categoryarray=['40 x 100', '80 x 100', '100 x 100', '1/2 acre', '1 acre', '2 acres', '2 acres +']  # Custom order for x-axis labels
    )
)

In [ ]:
labels = ['0- 4000', '4001-8000', '8001-10000', '10001-20000', '20001-43451', '43452-86900', '86901 +']
#
fig = go.Figure()

for town, group in houses.groupby('Town'):
    fig.add_trace(go.Scatter(x=group['jittered_x'], y=group['Sold_Price'],
                             mode='markers',
                             name=town,
                             marker=dict(color=color_dict.get(town, '#000000')),  # Using color_dict for colors
                             text=group['Town']))  # Hover text

# Update layout for custom x-axis labels, ensuring correct order
fig.update_layout(
    title='Sold Price vs Lot Square Footage by Category with Jitter',
    xaxis=dict(
        title="Lot Square Footage Category",
        tickmode='array',
        # Ensure tickvals correspond to the numeric mapping of your categories, assuming sequential mapping starting from 0
        tickvals=list(range(len(labels))),  # Sequential numeric values for each category
        ticktext=labels  # The labels in the order you specified
    ),
    yaxis_title="Sold Price",
    legend_title="Town"
)



fig.show()

In [ ]:
#########

In [ ]:
labels = ['0- 4000', '4001-8000', '8001-10000', '10001-20000', '20001-43451', '43452-86900', '86901 +']
#
fig = go.Figure()

for town, group in houses.groupby('Town'):
    fig.add_trace(go.Scatter(x=group['jittered_x'], y=group['Sold_Price'],
                             mode='markers',
                             name=town,
                             marker=dict(color=color_dict.get(town, '#000000')),  # Using color_dict for colors
                             text=group['Town']))  # Hover text

# Update layout for custom x-axis labels, ensuring correct order
fig.update_layout(
    title='Sold Price vs Lot Square Footage by Category with Jitter',
    xaxis=dict(
        title="Lot Square Footage Category",
        tickmode='array',
        # Ensure tickvals correspond to the numeric mapping of your categories, assuming sequential mapping starting from 0
        tickvals=list(range(len(labels))),  # Sequential numeric values for each category
        ticktext=labels  # The labels in the order you specified
    ),
    yaxis_title="Sold Price",
    legend_title="Town"
)

fig.show()


In [ ]:
import plotly.graph_objects as go
import numpy as np
import pandas as pd

# Ensure this color_dict is defined in your script or notebook
color_dict = {
    'Roslyns': '#006400',  # DarkGreen
    'Port Washington': '#008000',  # Green
    'Locust Valley': '#90EE90',  # LightGreen
    'Mineola': '#00008B',  # DarkBlue
    'Westbury': '#0000FF',  # Blue
    'Farmingdale': '#ADD8E6',  # LightBlue
    'Freeport': '#8B0000',  # DarkRed
    'Hempstead': '#FF0000',  # Red
    'Roosevelt': '#F08080'  # LightCoral
}

# Assuming your 'houses' DataFrame and category setup are correct and include a 'Lot_Square_Footage_Category'
# The rest of the setup for categorizing and adding jitter remains the same as in the previous example

# Plotting (ensure towns in 'houses' match keys in 'color_dict')
fig = go.Figure()

for town, group in houses.groupby('Town'):
    fig.add_trace(go.Scatter(x=group['jittered_x'], y=group['Sold_Price'],
                             mode='markers',
                             name=town,
                             marker=dict(color=color_dict.get(town, '#000000')),  # Default to black if not found
                             text=group['Town']))  # Hover text

# Custom x-axis labels setup remains the same
# ...

fig.show()




In [ ]:
######

In [ ]:
# Ensure the DataFrame 'houses' has 'Lot_Square_Footage_Category' in the correct order
houses['Lot_Square_Footage_Category'] = pd.Categorical(houses['Lot_Square_Footage_Category'],
                                                       categories=labels,
                                                       ordered=True)


In [ ]:
import plotly.express as px

fig = px.scatter(houses, x='Lot_Square_Footage_Category', y='Sold_Price',
                 color="Town",
                 color_discrete_map=color_dict,
                 hover_name="Town",
                 hover_data=["Lot_Square_Footage", "Sold_Price"],
                 title='Sold Price vs Lot Square Footage by Category',
                 opacity=0.5,  # Adjust opacity here (0 to 1)
                 size_max=10)  # Adjust maximum size of points

# Update layout
fig.update_layout(
    xaxis_title="Lot Square Footage Category",
    yaxis_title="Sold Price",
    legend_title="Town"
)

fig.update_traces(marker=dict(size=12))  # Adjust point size here

fig.show()


In [ ]:
'0- 4000','4001-8000','8001-10000','10001-20000','20001-43451','43452-86900', '86901 +'

In [ ]:
XXXX

In [ ]:
# Categorizing Lot Sq Footage

import pandas as pd

# Assuming 'houses' is your DataFrame
# Define the bins and labels for 'Lot_Square_Footage'
bins = [0, 4000, 8000, 10000, 20000, 43451, 86900, float('inf')]
labels = ['0-4000', '4001-8000', '8001-10000', '10001-20000', '20001-43451', '43452-86900', '86901+']

# Categorize 'Lot_Square_Footage' into discrete bins
houses['Lot_Square_Footage_Category'] = pd.cut(houses['Lot_Square_Footage'], bins=bins, labels=labels, right=False)

# Ensure the new column is of type 'category' for better handling by Plotly
houses['Lot_Square_Footage_Category'] = houses['Lot_Square_Footage_Category'].astype('category')


In [ ]:
# Plotting the categorized lot sq footage

import plotly.express as px

# Now use the categorized 'Lot_Square_Footage_Category' for the x-axis
fig = px.scatter(houses, x='Lot_Square_Footage_Category', y='Sold_Price',
                 color="Town",
                 color_discrete_map=color_dict,  # Your predefined color mapping
                 hover_name="Town",
                 hover_data=["Lot_Square_Footage", "Sold_Price"],
                 title='Sold Price vs Lot Square Footage by Category')

# Update layout if needed
fig.update_layout(
    xaxis_title="Lot Square Footage Category",
    yaxis_title="Sold Price",
    legend_title="Town"
)

fig.show()


In [ ]:
#######

In [ ]:
import plotly.express as px

data = houses

# Assuming the DataFrame is correctly named med_incomes
# Ensure the town names in your DataFrame match these keys exactly, e.g., 'Port_Washington' instead of 'Port Washington'
color_dict = {
    'Roslyns': '#006400',  # DarkGreen
    'Port_Washington': '#008000',  # Green
    'Locust_Valley': '#90EE90',  # LightGreen
    'Mineola': '#00008B',  # DarkBlue
    'Westbury': '#0000FF',  # Blue
    'Farmingdale': '#ADD8E6',  # LightBlue
    'Freeport': '#8B0000',  # DarkRed
    'Hempstead': '#FF0000',  # Red
    'Roosevelt': '#F08080'  # LightCoral
}

# Create the scatter plot
fig = px.scatter(houses, x='Lot_Square_Footage', y='Sold_Price',
                 color = "Town",
                 color_discrete_map=color_dict,
                 hover_name="Town",
                 hover_data=["Lot_Square_Footage", "Sold_Price"],
                 title='Sold Price vs Lot Square Footage')



fig.update_layout(
    title="Average Household Income by Town and Year",
    xaxis_title="Year",
    yaxis_title="Average Household Income",
    legend_title="Town"
)

fig.show()


In [ ]:
import pandas as pd
import plotly.express as px

# Assuming df is your DataFrame with 'Lot_Square_Footage' and 'Sold_Price' columns
# df = pd.read_csv('your_data.csv')  # Example to load data from a CSV file

# Create the scatter plot
fig = px.scatter(houses, x='Lot_Square_Footage', y='Sold_Price', title='Sold Price vs Lot Square Footage')

# Update layout with specific y-axis range
fig.update_layout(
    xaxis_title='Lot Square Footage',
    yaxis_title='Sold Price',
    plot_bgcolor='white',
    xaxis=dict(showline=True, showgrid=False, linecolor='black'),
    yaxis=dict(showline=True, showgrid=True, gridcolor='lightgrey', linecolor='black', range=[0, 3000000])  # Y-axis range set to 0 to $5 million
)

# Show the figure
fig.show()


In [ ]:
# prompt: CAN I SEE ALL of th unique of Town

houses['Town'].unique()


In [ ]:
# prompt: make a pltly histogram of  Lot_Square_Footage

fig = px.histogram(houses, x="Lot_Square_Footage", nbins=20, title="Distribution of Lot Square Footage")

# Update layout with specific y-axis range
fig.update_layout(
    xaxis_title='Lot Square Footage',
    yaxis_title='Frequency',
    plot_bgcolor='white',
    xaxis=dict(showline=True, showgrid=False, linecolor='black'),
    yaxis=dict(showline=True, showgrid=True, gridcolor='lightgrey', linecolor='black')
)

# Show the figure
fig.show()


In [ ]:
# Filter the DataFrame to exclude rows where Town is 'Freeport'
# and then check if there are any non-null entries in 'Lot_Square_Footage'
non_freeport_lot_sqft_not_null = data[data['Town'] != 'Freeport']['Lot_Square_Footage'].notnull().any()

print(non_freeport_lot_sqft_not_null)
